In [1]:
import os
import json
import re
def determine_file_type(filename):
    # Determine the file type based on the filename
    print(filename)
    if (
    (
        "other_unknown_abeta" in filename
        or "abeta_tau_known_abeta" in filename
    or  "abeta_known_tau_unknown_mmse_known_abeta" in filename)
    and "abeta_known_tau_unknown_mmse_known_abeta_rate" not in filename
    and "abeta_tau_known_abeta_rate" not in filename
):
        print("yes")
        return "abeta"
    elif "abeta_tau_known_meta_tau" in filename or "abeta_unknown_tau_known_meta_tau" in filename:
        return "meta_tau"
    elif "abeta_tau_known_mmse" in filename or "other_unknown_mmse" in filename or "abeta_known_tau_unknown_mmse_known_mmse" in filename:
        return "mmse"
    elif "abeta_tau_known_treatment" in filename:
        return "treatment"
    else:
        return None  # If the file does not match any known type

def extract_probabilities(file_path, file_type):
    # Define token sets based on the file type
    if file_type == "abeta":
        tokens = ['ĠClearly', 'ĠWeak', 'ĠIntermediate', 'ĠNegative']
    elif file_type == "meta_tau":
        tokens = ['ĠLow', 'ĠVery', 'ĠSuper', 'ĠHigh'] # Adjust based on your actual token names
    elif file_type == "mmse":
        tokens = ['ĠSlow', 'ĠModerate', 'ĠFast', 'ĠStable'] # Adjust based on your actual token names
    elif file_type == "treatment":
        tokens = ['Ġideal', 'Ġunlikely'] # Adjust based on your actual token names
    else:
        raise ValueError(f"Unsupported file type: {file_type}")

    position_probabilities = {}

    with open(file_path, "r") as json_file:
        data = json.load(json_file)
        print(json_file)
        # Gather positions for all tokens
        all_positions = set()
        for token in tokens:
            token_data = data.get(token, [])
            for entry in token_data:
                position = entry[0]
                all_positions.add(position)
                if position not in position_probabilities:
                    position_probabilities[position] = {}
                position_probabilities[position][token] = entry[1]
    if not all_positions:
        return 0
    # Determine the best position shared across all tokens
    best_position = None
    for position in sorted(all_positions):
        if all(token in position_probabilities[position] for token in tokens) :
            total_probability = sum(position_probabilities[position][token] for token in tokens)
            if total_probability > 0.5:
                best_position = position
                break
    print(best_position)
    # If no common position is found, fall back to the minimum position that has the most tokens covered

    if best_position is None:
        best_position = min(all_positions, key=lambda pos: (-sum(1 for token in tokens if token in position_probabilities[pos]), pos))


    # Collect probabilities for the chosen position, defaulting to 0 if a token is missing
    probabilities = {token: position_probabilities[best_position].get(token, 0.0) for token in tokens}

    # Normalize the probabilities to sum to 1
    total_probability = sum(probabilities.values())
    
    if total_probability == 0:
        # Handle case where no probability is found, set everything to zero
        normalized_probabilities = {token: 0.0 for token in tokens}
    else:
        # Normalize probabilities
        normalized_probabilities = {token: prob / total_probability for token, prob in probabilities.items()}

    return normalized_probabilities
def extract_abeta_index(filename):
    # Extract the index for abeta files, assuming it's the number before "_abeta"
    match = re.search(r'(\d+)', filename)
    if match:
        return int(match.group(1))
    return None

def process_abeta(directory):
    results = {
        "abeta": {},
        "meta_tau": {},
        "mmse": {},
        "treatment": {}
    }

    for filename in os.listdir(directory):
        if filename.endswith(".json"):
            file_path = os.path.join(directory, filename)
            file_type = determine_file_type(filename)
            if file_type:
                probabilities = extract_probabilities(file_path, file_type)
                if probabilities==0:
                    continue
                # Based on the file type, append probabilities to the correct category
                if file_type == "abeta":
                    abeta_index = extract_abeta_index(filename)
                    print(abeta_index)
                    if abeta_index is not None:
                        results["abeta"][abeta_index] = probabilities
                    if abeta_index is None:
                        results["abeta"][abeta_index] ={0,0,0,0}
#                 elif file_type == "ec_tau":
#                     results["ec_tau"].append(probabilities.get('ĠEC', 0))
#                     results["meta_tau"].append(probabilities.get('ĠMeta', 0))
#                 elif file_type == "mmse":
#                     mmse_index = extract_abeta_index(filename)
#                     if mmse_index is not None:
#                         results["mmse"][mmse_index] = probabilities

    return results

def process_mmse(directory):
    results = {
       "abeta": {},
        "meta_tau": {},
        "mmse": {},
        "treatment": {}
    }

    for filename in os.listdir(directory):
        if filename.endswith(".json"):
            file_path = os.path.join(directory, filename)
            file_type = determine_file_type(filename)
            print(file_type)
            if file_type=="mmse":
                probabilities = extract_probabilities(file_path, file_type)
                print(probabilities)
                # Based on the file type, append probabilities to the correct category
                if file_type == "mmse":
                    mmse_index = extract_abeta_index(filename)
                    print(mmse_index)
                    if mmse_index is not None:
                        results["mmse"][mmse_index] = probabilities
            

    return results



output_0other_unknown_abeta.json
yes
abeta
output_100other_unknown_abeta.json
yes
abeta
output_101abeta_tau_known_abeta.json
yes
abeta
output_101abeta_tau_known_meta_tau.json
meta_tau
output_101abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_101abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.4751729127006457, 'ĠModerate': 0.25039853608584917, 'ĠFast': 0.024030015127655954, 'ĠStable': 0.25039853608584917}
101
output_101abeta_tau_known_treatment.json
treatment
output_102abeta_tau_known_abeta.json
yes
abeta
output_102abeta_tau_known_meta_tau.json
meta_tau
output_102abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_102abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.3867236478667586, 'ĠModerate': 0.17431000999603602, 'ĠFast': 0.02081836116729315, 'ĠStable': 0.4

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_432other_unknown_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.2572528018147082, 'ĠModerate': 0.5361609056189491, 'ĠFast': 0.02977917670941263, 'ĠStable': 0.17680711585693004}
432
output_433abeta_tau_known_abeta.json
yes
abeta
output_433abeta_tau_known_meta_tau.json
meta_tau
output_433abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_433abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.47098168409252356, 'ĠModerate': 0.25209834067788384, 'ĠFast': 0.028730065905010586, 'ĠStable': 0.24818990932458201}
433
output_433abeta_tau_known_treatment.json
treatment
output_434other_unknown_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_434other_unknown_mmse.json' mode='r' encoding='cp93

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_731abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.44199849657270346, 'ĠModerate': 0.2598374935800447, 'ĠFast': 0.030078373811274515, 'ĠStable': 0.2680856360359773}
731
output_731abeta_tau_known_treatment.json
treatment
output_732other_unknown_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_732other_unknown_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.29903521781241865, 'ĠModerate': 0.5248231884223078, 'ĠFast': 0.03488733874160491, 'ĠStable': 0.14125425502366856}
732
output_733abeta_tau_known_abeta.json
yes
abeta
output_733abeta_tau_known_meta_tau.json
meta_tau
output_733abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_733abeta_tau_known_mmse.json' mode='r' encoding='cp9

### HABS-HD

In [2]:
# Usage example
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\"
extracted_probabilities = process_mmse(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")
import pandas as pd
# Filter out integer values and keep only dictionary entries
filtered_data = {k: v for k, v in extracted_probabilities['mmse'].items() if isinstance(v, dict)}

# Convert to DataFrame
df = pd.DataFrame.from_dict(filtered_data, orient='index')

# Rename the columns to match the requested format
df.columns = [
    "MMSE-Slow", "MMSE-Moderate", "MMSE-Fast", "MMSE-Not decreasing"
]

print(df)
df = df.sort_index(key=lambda x: x.astype(int))
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(742))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(742), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD-results\\HABS-HD_probability_MMSE.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


D:\ANACONDA\lib\site-packages\pandas\core\computation\expressions.py:21: UserWarning: Pandas requires version '2.8.4' or newer of 'numexpr' (version '2.7.3' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED
D:\ANACONDA\lib\site-packages\pandas\core\arrays\masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.2' currently installed).
  from pandas.core import (


     MMSE-Slow  MMSE-Moderate  MMSE-Fast  MMSE-Not decreasing
101   0.475173       0.250399   0.024030             0.250399
102   0.386724       0.174310   0.020818             0.418148
104   0.786014       0.169987   0.000000             0.043999
107   0.321228       0.590829   0.057593             0.030349
10    0.480384       0.191084   0.023181             0.305351
..         ...            ...        ...                  ...
8     0.410086       0.350765   0.127039             0.112111
92    0.339432       0.501649   0.075738             0.083181
93    0.398924       0.089012   0.007778             0.504287
95    0.391384       0.097423   0.008647             0.502547
9     0.494145       0.277190   0.049697             0.178967

[627 rows x 4 columns]


Missing indices: [0, 2, 5, 13, 15, 18, 19, 21, 25, 29, 30, 33, 40, 47, 48, 52, 53, 56, 57, 58, 61, 64, 65, 66, 68, 74, 77, 81, 83, 84, 85, 88, 89, 90, 91, 94, 96, 97, 98, 99, 100, 103, 105, 106, 108, 109, 110, 111, 112, 113, 115, 118, 122, 123, 127, 129, 131, 133, 141, 148, 150, 152, 155, 157, 158, 167, 169, 171, 173, 176, 177, 178, 179, 180, 181, 182, 185, 186, 189, 190, 191, 192, 194, 195, 196, 201, 204, 206, 208, 210, 211, 212, 213, 216, 217, 218, 219, 220, 222, 223, 227, 231, 233, 234, 235, 238, 239, 240, 241, 242, 243, 265, 400, 418, 666]
CSV file saved at: D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD-results\HABS-HD_probability_MMSE.csv


In [5]:
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\"
extracted_probabilities = process_abeta(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")

output_0other_unknown_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_0other_unknown_abeta.json' mode='r' encoding='cp936'>
5
0
output_100other_unknown_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_100other_unknown_abeta.json' mode='r' encoding='cp936'>
None
100
output_101abeta_tau_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_101abeta_tau_known_abeta.json' mode='r' encoding='cp936'>
5
101
output_101abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_101abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
None
output_101abeta_tau_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_330abeta_tau_known_abeta.json' mode='r' encoding='cp936'>
None
330
output_330abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_330abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
None
output_330abeta_tau_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_330abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
None
output_330abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_330abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
None
output_331other_unknown_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_331other_unk

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_611other_unknown_mmse.json' mode='r' encoding='cp936'>
3
output_612other_unknown_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_612other_unknown_mmse.json' mode='r' encoding='cp936'>
3
output_613abeta_tau_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_613abeta_tau_known_abeta.json' mode='r' encoding='cp936'>
5
613
output_613abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_613abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
None
output_613abeta_tau_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_613abeta_tau_known_mmse.json' 

In [6]:

import pandas as pd
df = pd.DataFrame.from_dict(extracted_probabilities['abeta'], orient='index')

# Rename the columns to match the requested format
df.columns = [
  "Abeta-Clearly positive","Abeta-Weakly positive","Abeta-Intermediate negative","Abeta-Negative"


]
df = df.sort_index(key=lambda x: x.astype(int))

In [7]:
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(742))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(742), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD-results\\HABS-HD_probability_abeta.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


Missing indices: [148, 237, 244, 245, 246, 247, 249, 251, 253, 255, 258, 260, 262, 264, 267, 269, 271, 273, 275, 277, 279, 281, 283, 285, 287, 289, 291, 293, 295, 297, 299, 303, 305, 309, 311, 315, 317, 319, 325, 329, 331, 333, 335, 337, 339, 341, 343, 345, 347, 349, 351, 353, 355, 358, 360, 361, 362, 363, 365, 366, 367, 368, 369, 371, 372, 373, 375, 376, 378, 380, 382, 386, 387, 389, 390, 392, 394, 396, 397, 399, 401, 402, 404, 406, 408, 409, 411, 413, 415, 417, 420, 422, 423, 425, 427, 429, 431, 432, 434, 436, 438, 440, 442, 444, 446, 447, 448, 450, 452, 453, 455, 456, 458, 461, 462, 464, 466, 467, 468, 470, 472, 474, 476, 478, 480, 481, 483, 484, 486, 487, 488, 492, 497, 498, 499, 500, 502, 504, 506, 507, 509, 513, 514, 516, 517, 518, 519, 520, 521, 522, 523, 531, 532, 534, 535, 537, 538, 540, 541, 542, 543, 547, 548, 550, 551, 552, 553, 555, 556, 557, 558, 559, 560, 561, 562, 564, 565, 567, 568, 569, 570, 572, 573, 574, 575, 577, 578, 580, 583, 584, 585, 586, 587, 588, 589, 590, 59

In [8]:
def process_tau(directory):
    results = {
        "abeta": {},
        "meta_tau": {},
        "mmse":{}
    }

    for filename in os.listdir(directory):
        if filename.endswith(".json"):
            file_path = os.path.join(directory, filename)
            file_type = determine_file_type(filename)
            print(file_path)
            if file_type == "meta_tau":
                probabilities = extract_probabilities(file_path, file_type)
                print(probabilities)
                if probabilities==0:
                    continue
                if not probabilities:
                    continue
                # Based on the file type, append probabilities to the correct category
                if file_type == "meta_tau":
                    meta_tau_index = extract_abeta_index(filename)
                    print(meta_tau_index)
                    if meta_tau_index is not None:
                        results["meta_tau"][meta_tau_index] = probabilities

    return results

In [9]:
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\"
extracted_probabilities = process_tau(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")

output_0other_unknown_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_0other_unknown_abeta.json
output_100other_unknown_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_100other_unknown_abeta.json
output_101abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_101abeta_tau_known_abeta.json
output_101abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_101abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_101abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
None
{'ĠLow': 0.3948756719000815, 'ĠVery': 0.44051563980349384, 'ĠSuper': 0.0, 'ĠHigh': 0.16460868829642464}
101
output_101abeta_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\out

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\output_594abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
5
{'ĠLow': 0.3010823650513118, 'ĠVery': 0.5713539077281938, 'ĠSuper': 7.744082745554064e-05, 'ĠHigh': 0.12748628639303883}
594
output_594abeta_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_594abeta_tau_known_mmse.json
output_594abeta_tau_known_treatment.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_594abeta_tau_known_treatment.json
output_595other_unknown_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_595other_unknown_mmse.json
output_596abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_596abeta_tau_known_abeta.json
output_596abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD

In [10]:
import pandas as pd
df_meta_tau = pd.DataFrame.from_dict(extracted_probabilities['meta_tau'], orient='index')

# Rename the columns to match the requested format
df_meta_tau .columns = [
  "Meta Tau-Low","Meta Tau-Very low","Meta Tau-Super high","Meta Tau-High"

]

In [11]:
df_meta_tau = df_meta_tau.sort_index(key=lambda x: x.astype(int))

In [12]:
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(742))
current_indices = set(df_meta_tau.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df_meta_tau.reindex(range(742), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full =  'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD-results\\HABS-HD_probability_meta_tau.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


Missing indices: [0, 2, 5, 13, 15, 18, 19, 21, 25, 29, 30, 33, 40, 47, 48, 52, 53, 56, 57, 58, 61, 64, 65, 66, 68, 74, 77, 81, 83, 84, 85, 88, 89, 90, 91, 94, 96, 97, 98, 99, 100, 103, 105, 106, 108, 109, 110, 111, 112, 113, 115, 118, 122, 123, 127, 129, 131, 133, 141, 148, 150, 152, 155, 157, 158, 167, 169, 171, 173, 176, 177, 178, 179, 180, 181, 182, 185, 186, 189, 190, 191, 192, 194, 195, 196, 201, 204, 206, 208, 210, 211, 212, 213, 216, 217, 218, 219, 220, 222, 223, 227, 231, 233, 234, 235, 237, 238, 239, 240, 241, 242, 243, 244, 245, 246, 247, 248, 249, 251, 253, 255, 258, 259, 260, 261, 262, 263, 264, 265, 266, 267, 268, 269, 271, 273, 275, 276, 277, 278, 279, 280, 281, 282, 283, 285, 286, 287, 289, 291, 293, 294, 295, 296, 297, 298, 299, 303, 305, 308, 309, 311, 315, 317, 318, 319, 320, 321, 322, 323, 324, 325, 329, 331, 332, 333, 335, 337, 338, 339, 341, 342, 343, 345, 347, 349, 350, 351, 353, 355, 358, 360, 361, 362, 363, 365, 366, 367, 368, 369, 370, 371, 372, 373, 374, 375, 

In [14]:
def process_treatment(directory):
    results = {
        "abeta": {},
        "meta_tau": {},
        "treatment":{}
    }

    for filename in os.listdir(directory):
        if filename.endswith(".json"):
            file_path = os.path.join(directory, filename)
            file_type = determine_file_type(filename)
            print(file_path)
            if file_type == "treatment":
                probabilities = extract_probabilities(file_path, file_type)
                print(probabilities)
                if probabilities==0:
                    continue
                if not probabilities:
                    continue
                # Based on the file type, append probabilities to the correct category
                if file_type == "treatment":
                    meta_tau_index = extract_abeta_index(filename)
                    print(meta_tau_index)
                    if meta_tau_index is not None:
                        results["treatment"][meta_tau_index] = probabilities

    return results

In [15]:
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\probability\\"
extracted_probabilities = process_treatment(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")

output_0other_unknown_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_0other_unknown_abeta.json
output_100other_unknown_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_100other_unknown_abeta.json
output_101abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_101abeta_tau_known_abeta.json
output_101abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_101abeta_tau_known_meta_tau.json
output_101abeta_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_101abeta_tau_known_mmse.json
output_101abeta_tau_known_treatment.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_101abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD\\proba

2
{'Ġideal': 0.7154239940696674, 'Ġunlikely': 0.2845760059303326}
566
output_567other_unknown_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_567other_unknown_mmse.json
output_568other_unknown_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_568other_unknown_mmse.json
output_569other_unknown_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_569other_unknown_mmse.json
output_56other_unknown_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_56other_unknown_abeta.json
output_570other_unknown_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_570other_unknown_mmse.json
output_571abeta_known_tau_unknown_mmse_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\HABS-HD\HABS-HD\probability\output_571abeta_known_tau_unknown_mmse_known_abeta.json
output_571abeta_known_tau_

In [16]:
import pandas as pd
df_treatment = pd.DataFrame.from_dict(extracted_probabilities['treatment'], orient='index')

# Rename the columns to match the requested format
df_treatment .columns = [
  "Treatment-Ideal","Treatment-Unlikely"

]

In [17]:
df_treatment = df_treatment.sort_index(key=lambda x: x.astype(int))

In [18]:
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(742))
current_indices = set(df_treatment.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df_treatment.reindex(range(742), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\HABS-HD\\HABS-HD-results\\HABS-HD_probability_treatment.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


Missing indices: [0, 2, 5, 13, 15, 18, 19, 21, 25, 29, 30, 33, 40, 47, 48, 52, 53, 56, 57, 58, 61, 64, 65, 66, 68, 74, 77, 81, 83, 84, 85, 88, 89, 90, 91, 94, 96, 97, 98, 99, 100, 103, 105, 106, 108, 109, 110, 111, 112, 113, 115, 118, 122, 123, 127, 129, 131, 133, 141, 148, 150, 152, 155, 157, 158, 167, 169, 171, 173, 176, 177, 178, 179, 180, 181, 182, 185, 186, 189, 190, 191, 192, 194, 195, 196, 201, 204, 206, 208, 210, 211, 212, 213, 216, 217, 218, 219, 220, 222, 223, 227, 231, 233, 234, 235, 237, 238, 239, 240, 241, 242, 243, 244, 245, 246, 247, 248, 249, 251, 253, 255, 258, 259, 260, 261, 262, 263, 264, 265, 266, 267, 268, 269, 271, 273, 275, 276, 277, 278, 279, 280, 281, 282, 283, 285, 286, 287, 289, 291, 293, 294, 295, 296, 297, 298, 299, 303, 305, 308, 309, 311, 315, 317, 318, 319, 320, 321, 322, 323, 324, 325, 329, 331, 332, 333, 335, 337, 338, 339, 341, 342, 343, 345, 347, 349, 350, 351, 353, 355, 358, 360, 361, 362, 363, 365, 366, 367, 368, 369, 370, 371, 372, 373, 374, 375, 

### ADNI

In [19]:
# Usage example
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\"
extracted_probabilities = process_mmse(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")
import pandas as pd
# Filter out integer values and keep only dictionary entries
filtered_data = {k: v for k, v in extracted_probabilities['mmse'].items() if isinstance(v, dict)}

# Convert to DataFrame
df = pd.DataFrame.from_dict(filtered_data, orient='index')

# Rename the columns to match the requested format
df.columns = [
    "MMSE-Slow", "MMSE-Moderate", "MMSE-Fast", "MMSE-Not decreasing"
]

print(df)
df = df.sort_index(key=lambda x: x.astype(int))
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(2464))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(2464), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI-results\\ADNI_probability_MMSE.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


output_0other_unknown_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_0other_unknown_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.46712663812544153, 'ĠModerate': 0.28332662454871077, 'ĠFast': 0.007204641189939143, 'ĠStable': 0.24234209613590857}
0
output_1000abeta_unknown_tau_known_meta_tau.json
meta_tau
output_1000abeta_unknown_tau_known_mmse.json
None
output_1001abeta_tau_known_abeta.json
yes
abeta
output_1001abeta_tau_known_meta_tau.json
meta_tau
output_1001abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1001abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.4577161938508762, 'ĠModerate': 0.11755124455018467, 'ĠFast': 0.027061831318532327, 'ĠStable': 0.39767073028040684}
1001
output_1001abeta_tau_known_treatment.json
treatment
output_1002abeta_unknown_tau_known_meta_tau.json
meta_tau
output_100

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1376abeta_known_tau_unknown_mmse_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.27062931636843957, 'ĠModerate': 0.513564180660542, 'ĠFast': 0.20428171587867625, 'ĠStable': 0.011524787092342245}
1376
output_1377abeta_tau_known_abeta.json
yes
abeta
output_1377abeta_tau_known_meta_tau.json
meta_tau
output_1377abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1377abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.237913933811234, 'ĠModerate': 0.5278351146628241, 'ĠFast': 0.19417970976130552, 'ĠStable': 0.04007124176463643}
1377
output_1377abeta_tau_known_treatment.json
treatment
output_1378other_unknown_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1378other_unknown_mmse.json' mode='r' enco

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1741other_unknown_mmse.json' mode='r' encoding='cp936'>
None
{'ĠSlow': 0.3593517924401238, 'ĠModerate': 0.3171268397225294, 'ĠFast': 0.020916782364759304, 'ĠStable': 0.3026045854725875}
1741
output_1742abeta_known_tau_unknown_mmse_known_abeta.json
yes
abeta
output_1742abeta_known_tau_unknown_mmse_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1742abeta_known_tau_unknown_mmse_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.36584622404813655, 'ĠModerate': 0.5079271782267947, 'ĠFast': 0.0882645047956787, 'ĠStable': 0.03796209292939007}
1742
output_1743other_unknown_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1743other_unknown_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.34501739921091823, 'ĠModerate': 0.3

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2095other_unknown_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.3766507935649072, 'ĠModerate': 0.32216649603518993, 'ĠFast': 0.012394538907906014, 'ĠStable': 0.2887881714919968}
2095
output_2096abeta_known_tau_unknown_mmse_known_abeta.json
yes
abeta
output_2096abeta_known_tau_unknown_mmse_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2096abeta_known_tau_unknown_mmse_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.3328967696409674, 'ĠModerate': 0.5662765138667173, 'ĠFast': 0.05434390948727615, 'ĠStable': 0.04648280700503919}
2096
output_2097other_unknown_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2097other_unknown_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.31251504227206, 'ĠModerate': 0.186611

meta_tau
output_2447abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2447abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.40111539788441214, 'ĠModerate': 0.5070573288043009, 'ĠFast': 0.050205473361238616, 'ĠStable': 0.041621799950048353}
2447
output_2447abeta_tau_known_treatment.json
treatment
output_2448other_unknown_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2448other_unknown_mmse.json' mode='r' encoding='cp936'>
6
{'ĠSlow': 0.26856429907551105, 'ĠModerate': 0.654397811936893, 'ĠFast': 0.04666948068392641, 'ĠStable': 0.030368408303669568}
2448
output_2449abeta_tau_known_abeta.json
yes
abeta
output_2449abeta_tau_known_meta_tau.json
meta_tau
output_2449abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2449abet

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_602other_unknown_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.2652789197102961, 'ĠModerate': 0.2033964124902056, 'ĠFast': 0.003754553128600675, 'ĠStable': 0.5275701146708976}
602
output_603other_unknown_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_603other_unknown_mmse.json' mode='r' encoding='cp936'>
None
{'ĠSlow': 0.35445368794783305, 'ĠModerate': 0.31773023515627574, 'ĠFast': 0.0, 'ĠStable': 0.3278160768958912}
603
output_604other_unknown_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_604other_unknown_mmse.json' mode='r' encoding='cp936'>
None
{'ĠSlow': 0.458597982748063, 'ĠModerate': 0.2695958335923815, 'ĠFast': 0.00639001477626428, 'ĠStable': 0.26541616888329117}
604
output_605other_unknown_mmse.json
mmse
<_io.Tex

6
{'ĠSlow': 0.23028491222503342, 'ĠModerate': 0.6768449740939484, 'ĠFast': 0.05643374831446092, 'ĠStable': 0.0364363653665573}
984
output_985other_unknown_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_985other_unknown_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.22932091933957058, 'ĠModerate': 0.4705359769581342, 'ĠFast': 0.1901137179658848, 'ĠStable': 0.11002938573641041}
985
output_986other_unknown_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_986other_unknown_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.49303394060221695, 'ĠModerate': 0.26805788082597437, 'ĠFast': 0.006015430776174691, 'ĠStable': 0.232892747795634}
986
output_987other_unknown_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_987other_unknown_mmse.json' mode='r' encoding='cp936

In [20]:
# Usage example
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\"
extracted_probabilities = process_abeta(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")
import pandas as pd
# Filter out integer values and keep only dictionary entries
filtered_data = {k: v for k, v in extracted_probabilities['abeta'].items() if isinstance(v, dict)}

# Convert to DataFrame

import pandas as pd
df = pd.DataFrame.from_dict(extracted_probabilities['abeta'], orient='index')

# Rename the columns to match the requested format
df.columns = [
  "Abeta-Clearly positive","Abeta-Weakly positive","Abeta-Intermediate negative","Abeta-Negative"


]
df = df.sort_index(key=lambda x: x.astype(int))
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(2464))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(2464), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI-results\\ADNI_probability_abeta.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


output_0other_unknown_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_0other_unknown_mmse.json' mode='r' encoding='cp936'>
3
output_1000abeta_unknown_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1000abeta_unknown_tau_known_meta_tau.json' mode='r' encoding='cp936'>
5
output_1000abeta_unknown_tau_known_mmse.json
output_1001abeta_tau_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1001abeta_tau_known_abeta.json' mode='r' encoding='cp936'>
5
1001
output_1001abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1001abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
5
output_1001abeta_tau_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI proces

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1377abeta_tau_known_abeta.json' mode='r' encoding='cp936'>
5
1377
output_1377abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1377abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
5
output_1377abeta_tau_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1377abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
output_1377abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1377abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
output_1378other_unknown_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1378other_unknown_mmse.json' mode='r' encodin

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1781other_unknown_mmse.json' mode='r' encoding='cp936'>
None
output_1782abeta_known_tau_unknown_mmse_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1782abeta_known_tau_unknown_mmse_known_abeta.json' mode='r' encoding='cp936'>
5
1782
output_1782abeta_known_tau_unknown_mmse_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1782abeta_known_tau_unknown_mmse_known_mmse.json' mode='r' encoding='cp936'>
3
output_1783other_unknown_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1783other_unknown_abeta.json' mode='r' encoding='cp936'>
5
1783
output_1784other_unknown_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2133abeta_tau_known_abeta.json' mode='r' encoding='cp936'>
5
2133
output_2133abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2133abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
5
output_2133abeta_tau_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2133abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
output_2133abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2133abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
output_2134other_unknown_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2134other_unknown_mmse.json' mode='r' encodin

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2353abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
output_2353abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2353abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
output_2354other_unknown_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2354other_unknown_mmse.json' mode='r' encoding='cp936'>
3
output_2355other_unknown_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2355other_unknown_mmse.json' mode='r' encoding='cp936'>
3
output_2356abeta_tau_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2356abeta_tau_known_abeta.json' mode='r' encoding='cp936'>
5

3
output_529abeta_known_tau_unknown_mmse_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_529abeta_known_tau_unknown_mmse_known_abeta.json' mode='r' encoding='cp936'>
5
529
output_529abeta_known_tau_unknown_mmse_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_529abeta_known_tau_unknown_mmse_known_mmse.json' mode='r' encoding='cp936'>
3
output_52other_unknown_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_52other_unknown_mmse.json' mode='r' encoding='cp936'>
3
output_530abeta_known_tau_unknown_mmse_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_530abeta_known_tau_unknown_mmse_known_abeta.json' mode='r' encoding='cp936'>
5
530
output_530abeta_known_tau_unknown_mmse_known_mmse.json

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_973other_unknown_mmse.json' mode='r' encoding='cp936'>
3
output_974other_unknown_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_974other_unknown_mmse.json' mode='r' encoding='cp936'>
3
output_975other_unknown_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_975other_unknown_mmse.json' mode='r' encoding='cp936'>
3
output_976other_unknown_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_976other_unknown_mmse.json' mode='r' encoding='cp936'>
None
output_977other_unknown_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_977other_unknown_mmse.json' mode='r' encoding='cp936'>
3
output_978other_unknown_mmse.js

In [21]:
# Usage example
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\"
extracted_probabilities = process_tau(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")
import pandas as pd
# Filter out integer values and keep only dictionary entries
filtered_data = {k: v for k, v in extracted_probabilities['meta_tau'].items() if isinstance(v, dict)}

# Convert to DataFrame

import pandas as pd
df = pd.DataFrame.from_dict(extracted_probabilities['meta_tau'], orient='index')

# Rename the columns to match the requested format
df.columns = [
  "Meta Tau-Low","Meta Tau-Very low","Meta Tau-Super high","Meta Tau-High"

]
df = df.sort_index(key=lambda x: x.astype(int))
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(2464))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(2464), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI-results\\ADNI_probability_meta_tau.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


output_0other_unknown_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_0other_unknown_mmse.json
output_1000abeta_unknown_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_1000abeta_unknown_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1000abeta_unknown_tau_known_meta_tau.json' mode='r' encoding='cp936'>
5
{'ĠLow': 0.16088737054226956, 'ĠVery': 0.41084031222792444, 'ĠSuper': 0.04830714805824786, 'ĠHigh': 0.3799651691715581}
1000
output_1000abeta_unknown_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_1000abeta_unknown_tau_known_mmse.json
output_1001abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_1001abeta_tau_known_abeta.json
output_1001abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADN

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2009abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
5
{'ĠLow': 0.3102212801434874, 'ĠVery': 0.4656972458763168, 'ĠSuper': 0.0006374915879256514, 'ĠHigh': 0.22344398239227017}
2009
output_2009abeta_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_2009abeta_tau_known_mmse.json
output_2009abeta_tau_known_treatment.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_2009abeta_tau_known_treatment.json
output_200other_unknown_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_200other_unknown_mmse.json
output_2010other_unknown_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_2010other_unknown_mmse.json
output_2011abeta_known_tau_unknown_mmse_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\outp

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2344abeta_unknown_tau_known_meta_tau.json' mode='r' encoding='cp936'>
5
{'ĠLow': 0.296256235761709, 'ĠVery': 0.3686968340252721, 'ĠSuper': 0.009673108447296332, 'ĠHigh': 0.32537382176572255}
2344
output_2344abeta_unknown_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_2344abeta_unknown_tau_known_mmse.json
output_2345abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_2345abeta_tau_known_abeta.json
output_2345abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_2345abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2345abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
5
{'ĠLow': 0.332492141969579, 'ĠVery': 0.48377318558455146, 'ĠSuper'

In [22]:
# Usage example
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\"
extracted_probabilities = process_treatment(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")
import pandas as pd
# Filter out integer values and keep only dictionary entries
filtered_data = {k: v for k, v in extracted_probabilities['treatment'].items() if isinstance(v, dict)}

# Convert to DataFrame

import pandas as pd
df = pd.DataFrame.from_dict(extracted_probabilities['treatment'], orient='index')

# Rename the columns to match the requested format
df.columns = [
  "Treatment-Ideal","Treatment-Unlikely"

]
df = df.sort_index(key=lambda x: x.astype(int))
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(2464))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(2464), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI-results\\ADNI_probability_treatment.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


output_0other_unknown_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_0other_unknown_mmse.json
output_1000abeta_unknown_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_1000abeta_unknown_tau_known_meta_tau.json
output_1000abeta_unknown_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_1000abeta_unknown_tau_known_mmse.json
output_1001abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_1001abeta_tau_known_abeta.json
output_1001abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_1001abeta_tau_known_meta_tau.json
output_1001abeta_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_1001abeta_tau_known_mmse.json
output_1001abeta_tau_known_treatment.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probab

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_1961abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
{'Ġideal': 0.1895211046716376, 'Ġunlikely': 0.8104788953283624}
1961
output_1962abeta_unknown_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_1962abeta_unknown_tau_known_meta_tau.json
output_1962abeta_unknown_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_1962abeta_unknown_tau_known_mmse.json
output_1963other_unknown_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_1963other_unknown_abeta.json
output_1964other_unknown_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_1964other_unknown_mmse.json
output_1965abeta_known_tau_unknown_mmse_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_1965abeta_known

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\ADNI\\ADNI\\probability\\output_2400abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
{'Ġideal': 0.16026603809814363, 'Ġunlikely': 0.8397339619018563}
2400
output_2401abeta_unknown_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_2401abeta_unknown_tau_known_meta_tau.json
output_2401abeta_unknown_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_2401abeta_unknown_tau_known_mmse.json
output_2402abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_2402abeta_tau_known_abeta.json
output_2402abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_2402abeta_tau_known_meta_tau.json
output_2402abeta_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\ADNI\ADNI\probability\output_2402abeta_tau_known_mm

## POINTER

In [23]:
# Usage example
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\"
extracted_probabilities = process_mmse(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")
import pandas as pd
# Filter out integer values and keep only dictionary entries
filtered_data = {k: v for k, v in extracted_probabilities['mmse'].items() if isinstance(v, dict)}

# Convert to DataFrame
df = pd.DataFrame.from_dict(filtered_data, orient='index')

# Rename the columns to match the requested format
df.columns = [
    "MMSE-Slow", "MMSE-Moderate", "MMSE-Fast", "MMSE-Not decreasing"
]

print(df)
df = df.sort_index(key=lambda x: x.astype(int))
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(188))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(188), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER-results\\POINTER_probability_MMSE.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


output_0abeta_tau_known_abeta.json
yes
abeta
output_0abeta_tau_known_meta_tau.json
meta_tau
output_0abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\output_0abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.3327034283253815, 'ĠModerate': 0.07423616578725685, 'ĠFast': 0.009147691023821168, 'ĠStable': 0.5839127148635405}
0
output_0abeta_tau_known_treatment.json
treatment
output_100abeta_tau_known_abeta.json
yes
abeta
output_100abeta_tau_known_meta_tau.json
meta_tau
output_100abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\output_100abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.3404185107966794, 'ĠModerate': 0.1333098076180783, 'ĠFast': 0.023165770189727677, 'ĠStable': 0.5031059113955146}
100
output_100abeta_tau_known_treatment.json
treatment
output_101abeta_tau_known_abe

In [25]:
# Usage example
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\"
extracted_probabilities = process_abeta(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")
import pandas as pd
# Filter out integer values and keep only dictionary entries
filtered_data = {k: v for k, v in extracted_probabilities['abeta'].items() if isinstance(v, dict)}

# Convert to DataFrame

import pandas as pd
df = pd.DataFrame.from_dict(extracted_probabilities['abeta'], orient='index')

# Rename the columns to match the requested format
df.columns = [
  "Abeta-Clearly positive","Abeta-Weakly positive","Abeta-Intermediate negative","Abeta-Negative"


]
df = df.sort_index(key=lambda x: x.astype(int))
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(188))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(188), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER-results\\POINTER_probability_abeta.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


output_0abeta_tau_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\output_0abeta_tau_known_abeta.json' mode='r' encoding='cp936'>
5
0
output_0abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\output_0abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
None
output_0abeta_tau_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\output_0abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
output_0abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\output_0abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
output_100abeta_tau_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\output_8abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
None
output_8abeta_tau_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\output_8abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
output_8abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\output_8abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
output_90abeta_tau_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\output_90abeta_tau_known_abeta.json' mode='r' encoding='cp936'>
None
90
output_90abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\output_90abeta_tau_known_meta_ta

In [26]:
# Usage example
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\"
extracted_probabilities = process_tau(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")
import pandas as pd
# Filter out integer values and keep only dictionary entries
filtered_data = {k: v for k, v in extracted_probabilities['meta_tau'].items() if isinstance(v, dict)}

# Convert to DataFrame

import pandas as pd
df = pd.DataFrame.from_dict(extracted_probabilities['meta_tau'], orient='index')

# Rename the columns to match the requested format
df.columns = [
  "Meta Tau-Low","Meta Tau-Very low","Meta Tau-Super high","Meta Tau-High"

]
df = df.sort_index(key=lambda x: x.astype(int))
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(188))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(188), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER-results\\POINTER_probability_meta_tau.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


output_0abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\POINTER\POINTER\probability\output_0abeta_tau_known_abeta.json
output_0abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\POINTER\POINTER\probability\output_0abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\output_0abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
None
{'ĠLow': 0.3861363937874467, 'ĠVery': 0.5115476451015757, 'ĠSuper': 0.0, 'ĠHigh': 0.10231596111097757}
0
output_0abeta_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\POINTER\POINTER\probability\output_0abeta_tau_known_mmse.json
output_0abeta_tau_known_treatment.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\POINTER\POINTER\probability\output_0abeta_tau_known_treatment.json
output_100abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\POINTER\POINTER\probability\output_10

In [27]:
# Usage example
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\"
extracted_probabilities = process_treatment(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")
import pandas as pd
# Filter out integer values and keep only dictionary entries
filtered_data = {k: v for k, v in extracted_probabilities['treatment'].items() if isinstance(v, dict)}

# Convert to DataFrame

import pandas as pd
df = pd.DataFrame.from_dict(extracted_probabilities['treatment'], orient='index')

# Rename the columns to match the requested format
df.columns = [
  "Treatment-Ideal","Treatment-Unlikely"

]
df = df.sort_index(key=lambda x: x.astype(int))
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(188))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(188), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER-results\\POINTER_probability_treatment.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


output_0abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\POINTER\POINTER\probability\output_0abeta_tau_known_abeta.json
output_0abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\POINTER\POINTER\probability\output_0abeta_tau_known_meta_tau.json
output_0abeta_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\POINTER\POINTER\probability\output_0abeta_tau_known_mmse.json
output_0abeta_tau_known_treatment.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\POINTER\POINTER\probability\output_0abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\POINTER\\POINTER\\probability\\output_0abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
{'Ġideal': 0.6548947064440354, 'Ġunlikely': 0.34510529355596464}
0
output_100abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\POINTER\POINTER\probability\output_100abeta_tau_known_abeta.json
output_100ab

## A4

In [28]:
# Usage example
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\"
extracted_probabilities = process_mmse(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")
import pandas as pd
# Filter out integer values and keep only dictionary entries
filtered_data = {k: v for k, v in extracted_probabilities['mmse'].items() if isinstance(v, dict)}

# Convert to DataFrame
df = pd.DataFrame.from_dict(filtered_data, orient='index')

# Rename the columns to match the requested format
df.columns = [
    "MMSE-Slow", "MMSE-Moderate", "MMSE-Fast", "MMSE-Not decreasing"
]

print(df)
df = df.sort_index(key=lambda x: x.astype(int))
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(440))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(440), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4-results\\A4_probability_MMSE.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


output_0abeta_tau_known_abeta.json
yes
abeta
output_0abeta_tau_known_meta_tau.json
meta_tau
output_0abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_0abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.5037907965192039, 'ĠModerate': 0.11780563635130147, 'ĠFast': 0.009822357612991155, 'ĠStable': 0.36858120951650347}
0
output_0abeta_tau_known_treatment.json
treatment
output_100abeta_tau_known_abeta.json
yes
abeta
output_100abeta_tau_known_meta_tau.json
meta_tau
output_100abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_100abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.4789020065518839, 'ĠModerate': 0.10038331584314836, 'ĠFast': 0.011088083397831641, 'ĠStable': 0.40962659420713604}
100
output_100abeta_tau_known_treatment.json
treatment
output_101abeta_tau_known_abeta.json
yes
abeta

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_319abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.5124489447875398, 'ĠModerate': 0.15386507180724154, 'ĠFast': 0.022870000815724743, 'ĠStable': 0.3108159825894939}
319
output_319abeta_tau_known_treatment.json
treatment
output_31abeta_tau_known_abeta.json
yes
abeta
output_31abeta_tau_known_meta_tau.json
meta_tau
output_31abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_31abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
{'ĠSlow': 0.4969823624964827, 'ĠModerate': 0.10255810206271222, 'ĠFast': 0.007314103912140286, 'ĠStable': 0.39314543152866477}
31
output_31abeta_tau_known_treatment.json
treatment
output_320abeta_tau_known_abeta.json
yes
abeta
output_320abeta_tau_known_meta_tau.json
meta_tau
output_320abeta_tau_known_mmse.json
mmse
<_io.TextIOWrapper name='D:\\Research\\AD

In [29]:
# Usage example
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\"
extracted_probabilities = process_abeta(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")
import pandas as pd
# Filter out integer values and keep only dictionary entries
filtered_data = {k: v for k, v in extracted_probabilities['abeta'].items() if isinstance(v, dict)}

# Convert to DataFrame

import pandas as pd
df = pd.DataFrame.from_dict(extracted_probabilities['abeta'], orient='index')

# Rename the columns to match the requested format
df.columns = [
  "Abeta-Clearly positive","Abeta-Weakly positive","Abeta-Intermediate negative","Abeta-Negative"


]
df = df.sort_index(key=lambda x: x.astype(int))
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(440))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(440), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4-results\\A4_probability_abeta.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


output_0abeta_tau_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_0abeta_tau_known_abeta.json' mode='r' encoding='cp936'>
5
0
output_0abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_0abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
None
output_0abeta_tau_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_0abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
output_0abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_0abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
output_100abeta_tau_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_100abeta_tau_known_abeta.json' mode='r' e

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_236abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
output_236abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_236abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
output_237abeta_tau_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_237abeta_tau_known_abeta.json' mode='r' encoding='cp936'>
5
237
output_237abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_237abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
None
output_237abeta_tau_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_237abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
outpu

5
366
output_366abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_366abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
None
output_366abeta_tau_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_366abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
output_366abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_366abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
output_367abeta_tau_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_367abeta_tau_known_abeta.json' mode='r' encoding='cp936'>
5
367
output_367abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_367abeta_tau_known

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_95abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
output_96abeta_tau_known_abeta.json
yes
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_96abeta_tau_known_abeta.json' mode='r' encoding='cp936'>
5
96
output_96abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_96abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
None
output_96abeta_tau_known_mmse.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_96abeta_tau_known_mmse.json' mode='r' encoding='cp936'>
3
output_96abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_96abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
output_97a

In [30]:
# Usage example
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\"
extracted_probabilities = process_tau(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")
import pandas as pd
# Filter out integer values and keep only dictionary entries
filtered_data = {k: v for k, v in extracted_probabilities['meta_tau'].items() if isinstance(v, dict)}

# Convert to DataFrame

import pandas as pd
df = pd.DataFrame.from_dict(extracted_probabilities['meta_tau'], orient='index')

# Rename the columns to match the requested format
df.columns = [
  "Meta Tau-Low","Meta Tau-Very low","Meta Tau-Super high","Meta Tau-High"

]
df = df.sort_index(key=lambda x: x.astype(int))
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(440))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(440), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4-results\\A4_probability_meta_tau.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


output_0abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_0abeta_tau_known_abeta.json
output_0abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_0abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_0abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
None
{'ĠLow': 0.40357009084288425, 'ĠVery': 0.5181942796686262, 'ĠSuper': 0.0, 'ĠHigh': 0.07823562948848953}
0
output_0abeta_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_0abeta_tau_known_mmse.json
output_0abeta_tau_known_treatment.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_0abeta_tau_known_treatment.json
output_100abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_100abeta_tau_known_abeta.json
output_100abeta_tau_known_meta_

None
{'ĠLow': 0.33380422266759174, 'ĠVery': 0.533417622278783, 'ĠSuper': 0.0, 'ĠHigh': 0.1327781550536253}
328
output_328abeta_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_328abeta_tau_known_mmse.json
output_328abeta_tau_known_treatment.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_328abeta_tau_known_treatment.json
output_329abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_329abeta_tau_known_abeta.json
output_329abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_329abeta_tau_known_meta_tau.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_329abeta_tau_known_meta_tau.json' mode='r' encoding='cp936'>
None
{'ĠLow': 0.37203543545387513, 'ĠVery': 0.5246540597944821, 'ĠSuper': 0.0, 'ĠHigh': 0.1033105047516428}
329
output_329abeta_tau_known_mmse.json
D:\Rese

In [31]:
# Usage example
directory_path ="D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\"
extracted_probabilities = process_treatment(directory_path)

# Displaying the result
for biomarker, probs in extracted_probabilities.items():
    print(f"Biomarker: {biomarker}, Probabilities: {probs}")
import pandas as pd
# Filter out integer values and keep only dictionary entries
filtered_data = {k: v for k, v in extracted_probabilities['treatment'].items() if isinstance(v, dict)}

# Convert to DataFrame

import pandas as pd
df = pd.DataFrame.from_dict(extracted_probabilities['treatment'], orient='index')

# Rename the columns to match the requested format
df.columns = [
  "Treatment-Ideal","Treatment-Unlikely"

]
df = df.sort_index(key=lambda x: x.astype(int))
import pandas as pd

# Assuming df is the DataFrame already created from the earlier steps

# Step 1: Identify the missing indices in the original DataFrame
expected_indices = set(range(440))
current_indices = set(df.index)
missing_indices = sorted(list(expected_indices - current_indices))

print(f"Missing indices: {missing_indices}")

# Step 2: Reindex the DataFrame to include all indices from 0 to 2159
# Fill missing indices with 0
df_full = df.reindex(range(440), fill_value=0)

# Step 3: Save the updated DataFrame to a CSV file
csv_path_full = 'D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4-results\\A4_probability_treatment.csv'
df_full.to_csv(csv_path_full, index_label='Index')

print(f"CSV file saved at: {csv_path_full}")


output_0abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_0abeta_tau_known_abeta.json
output_0abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_0abeta_tau_known_meta_tau.json
output_0abeta_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_0abeta_tau_known_mmse.json
output_0abeta_tau_known_treatment.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_0abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_0abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
{'Ġideal': 0.6297746160955356, 'Ġunlikely': 0.3702253839044644}
0
output_100abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_100abeta_tau_known_abeta.json
output_100abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process

<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_309abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
{'Ġideal': 0.5273165265038204, 'Ġunlikely': 0.47268347349617956}
309
output_30abeta_tau_known_abeta.json
yes
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_30abeta_tau_known_abeta.json
output_30abeta_tau_known_meta_tau.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_30abeta_tau_known_meta_tau.json
output_30abeta_tau_known_mmse.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_30abeta_tau_known_mmse.json
output_30abeta_tau_known_treatment.json
D:\Research\AD\ADLLM\ADNI process 9\Zero-shot\A4\A4\probability\output_30abeta_tau_known_treatment.json
<_io.TextIOWrapper name='D:\\Research\\AD\\ADLLM\\ADNI process 9\\Zero-shot\\A4\\A4\\probability\\output_30abeta_tau_known_treatment.json' mode='r' encoding='cp936'>
2
{'Ġideal': 0.10669059979459383, 'Ġ